In [3]:
import xml.etree.ElementTree as ET
from PIL import Image
import numpy as np
import cv2
import os

def parse_xml(xml_file):
    tree = ET.parse(xml_file)
    root = tree.getroot()
    spaces = []

    for space in root.findall('space'):
        space_id = space.get('id')
        occupied = space.get('occupied')
        
        rotated_rect = space.find('rotatedRect')
        center_x = int(rotated_rect.find('center').get('x'))
        center_y = int(rotated_rect.find('center').get('y'))
        width = int(rotated_rect.find('size').get('w'))
        height = int(rotated_rect.find('size').get('h'))
        angle = float(rotated_rect.find('angle').get('d'))
        
        contour_points = []
        for point in space.findall('contour/point'):
            x = int(point.get('x'))
            y = int(point.get('y'))
            contour_points.append((x, y))
        
        spaces.append({
            'space_id': space_id,
            'occupied': occupied,
            'center': (center_x, center_y),
            'size': (width, height),
            'angle': angle,
            'contour': contour_points
        })
    
    return spaces

In [5]:
def rotate_and_crop_image(image, space):
    angle = space['angle']
    if abs(angle) < 45: 
        angle = 0
    else:
        angle = 90

    center = space['center']
    size = space['size']

    rect = ((center[0], center[1]), (size[0], size[1]), angle)
    box = cv2.boxPoints(rect)
    box = np.int32(box)  
    
    mask = np.zeros(image.shape[:2], dtype=np.uint8)
    cv2.fillPoly(mask, [box], 255)
    
    masked_image = cv2.bitwise_and(image, image, mask=mask)
    
    x, y, w, h = cv2.boundingRect(box)
    cropped_image = masked_image[y:y+h, x:x+w]

    return cropped_image

In [7]:
def process_images_in_folder(folder_path):
    for dirpath, dirnames, filenames in os.walk(folder_path):
        for filename in filenames:
            if filename.endswith('.xml'):
                xml_file = os.path.join(dirpath, filename)

                image_path = os.path.splitext(xml_file)[0] + '.jpg'  
                image = cv2.imread(image_path)

                if image is None:
                    print(f"Erro: A imagem {image_path} não foi encontrada.")
                    continue

                spaces = parse_xml(xml_file)

                occupied_folder = os.path.join(dirpath, 'occupied')
                empty_folder = os.path.join(dirpath, 'empty')

                os.makedirs(occupied_folder, exist_ok=True)
                os.makedirs(empty_folder, exist_ok=True)

                for space in spaces:
                    # Processar a imagem e recortar conforme o espaço
                    cropped_image = rotate_and_crop_image(image, space)

                    # Definir o diretório de saída baseado no campo 'occupied'
                    if space['occupied'] == '1':
                        output_folder = occupied_folder
                    else:
                        output_folder = empty_folder

                    # Nome da imagem será o nome do arquivo XML + space_id
                    base_name = os.path.splitext(filename)[0]  # Nome base do XML
                    output_filename = f"{base_name}_space_{space['space_id']}.png"
                    output_path = os.path.join(output_folder, output_filename)

                    # Salvar a imagem recortada
                    cv2.imwrite(output_path, cropped_image)
                    print(f"Imagem do espaço {space['space_id']} salva em {output_path}")

In [ ]:
parent_folder = 'PKLOT' 
process_images_in_folder(parent_folder)

Imagem do espaço 1 salva em PKLOT\PKLot\PUCPR\Cloudy\2012-09-12\empty\2012-09-12_06_05_16_space_1.png
Imagem do espaço 2 salva em PKLOT\PKLot\PUCPR\Cloudy\2012-09-12\empty\2012-09-12_06_05_16_space_2.png
Imagem do espaço 3 salva em PKLOT\PKLot\PUCPR\Cloudy\2012-09-12\empty\2012-09-12_06_05_16_space_3.png
Imagem do espaço 4 salva em PKLOT\PKLot\PUCPR\Cloudy\2012-09-12\empty\2012-09-12_06_05_16_space_4.png
Imagem do espaço 5 salva em PKLOT\PKLot\PUCPR\Cloudy\2012-09-12\empty\2012-09-12_06_05_16_space_5.png
Imagem do espaço 6 salva em PKLOT\PKLot\PUCPR\Cloudy\2012-09-12\empty\2012-09-12_06_05_16_space_6.png
Imagem do espaço 7 salva em PKLOT\PKLot\PUCPR\Cloudy\2012-09-12\empty\2012-09-12_06_05_16_space_7.png
Imagem do espaço 8 salva em PKLOT\PKLot\PUCPR\Cloudy\2012-09-12\empty\2012-09-12_06_05_16_space_8.png
Imagem do espaço 9 salva em PKLOT\PKLot\PUCPR\Cloudy\2012-09-12\empty\2012-09-12_06_05_16_space_9.png
Imagem do espaço 10 salva em PKLOT\PKLot\PUCPR\Cloudy\2012-09-12\empty\2012-09-12_